In [1]:
# !pip install "dask[complete]"    
# !pip install "dask[array]"       
# !pip install "dask[dataframe]"   
# !pip install "dask[diagnostics]" 
# !pip install "dask[distributed]"
# !pip install metpy
# !pip install zarr


# !pip install geemap xarray rioxarray netcdf4 localtileserver

In [43]:
import os
os.environ['USE_PYGEOS'] = '0'
import zarr
import fsspec
import xarray as xr
import hvplot.xarray
import intake
import metpy
import cartopy.crs as ccrs
import intake
import matplotlib.pyplot as plt
import numpy as np
import geoviews as gv
import geopandas as gpd
from shapely.geometry import Polygon
import rasterio
import geopandas as gpd
import xarray as xr
import hvplot.xarray
from rasterio.crs import CRS
import cartopy.crs as ccrs
from rasterio.mask import mask


In [3]:
# Define the feature collections

 
WATERSHED = "Ioway Creek" #------------> Specified the watershed from the asset
    
##==============================================================================================================================================================##
##==============================================================================================================================================================##

polygonFC = gpd.read_file(f'C:\\Users\\adi10136\\Desktop\\Runoff Analysis\\Shp\\{WATERSHED}\\layers\\globalwatershed.shp')

##==============================================================================================================================================================##
##==============================================================================================================================================================##

FC = polygonFC.to_crs(epsg=4326)  # Convert to WGS84 coordinate reference system
coordinates = FC['geometry'].iloc[0].__geo_interface__['coordinates'][0]  # Get the coordinates
print(coordinates)
# Create an Earth Engine polygon using the coordinates
# ee_polygonFC = ee.Geometry.Polygon(coordinates)

# Function to calculate mean within the polygon feature collection (FC)
def calculate_mean(image):
    mean_dict = image.reduceRegion(reducer=ee.Reducer.mean(), geometry=ee_polygonFC, scale=30)
    return mean_dict


((-93.79713650267362, 42.32456378704344), (-93.79713536578073, 42.324473734198016), (-93.79664994967764, 42.324477107767095), (-93.7966488134821, 42.32438705490967), (-93.79628475186925, 42.324389583730195), (-93.796283616198, 42.32429953086338), (-93.79604090877616, 42.32430121609639), (-93.79603977345619, 42.32421116322284), (-93.79579706635963, 42.32421284793691), (-93.79579593139088, 42.324122795056645), (-93.7955532246196, 42.32412447925178), (-93.79555209000213, 42.3240344263648), (-93.79543073678174, 42.32403526826709), (-93.79542960234248, 42.323945215376), (-93.79518689623214, 42.323946898790126), (-93.79518576214416, 42.32385684589233), (-93.79494305635909, 42.323858528787525), (-93.79494192262234, 42.323768475882964), (-93.7946992171626, 42.32377015825923), (-93.7946980837771, 42.32368010534799), (-93.79445537864264, 42.32368178720536), (-93.79445424560836, 42.32359173428736), (-93.79178449156804, 42.323610200760044), (-93.7917833623455, 42.32352014778269), (-93.791419305301

In [4]:
# open the hytest data intake catalog
hytest_cat = intake.open_catalog("https://raw.githubusercontent.com/hytest-org/hytest/main/dataset_catalog/hytest_intake_catalog.yml")
list(hytest_cat)

['conus404-catalog',
 'conus404-drb-eval-tutorial-catalog',
 'nhm-v1.0-daymet-catalog',
 'nhm-v1.1-c404-bc-catalog',
 'nhm-v1.1-gridmet-catalog',
 'trends-and-drivers-catalog',
 'nhm-prms-v1.1-gridmet-format-testing-catalog',
 'nwis-streamflow-usgs-gages-onprem',
 'nwis-streamflow-usgs-gages-osn',
 'nwm21-streamflow-usgs-gages-onprem',
 'nwm21-streamflow-usgs-gages-osn',
 'nwm21-streamflow-cloud',
 'geofabric_v1_1-zip-osn',
 'geofabric_v1_1_POIs_v1_1-osn',
 'geofabric_v1_1_TBtoGFv1_POIs-osn',
 'geofabric_v1_1_nhru_v1_1-osn',
 'geofabric_v1_1_nhru_v1_1_simp-osn',
 'geofabric_v1_1_nsegment_v1_1-osn',
 'gages2_nndar-osn',
 'wbd-zip-osn',
 'huc12-geoparquet-osn',
 'huc12-gpkg-osn',
 'nwm21-scores',
 'lcmap-cloud',
 'rechunking-tutorial-osn',
 'pointsample-tutorial-sites-osn',
 'pointsample-tutorial-output-osn']

In [5]:
# open the conus404 sub-catalog
cat = hytest_cat['conus404-catalog']
cat2 = hytest_cat['nhm-v1.0-daymet-catalog']
cat3 = hytest_cat['nhm-v1.1-gridmet-catalog']
list(cat)
list(cat2)

['nhm-v1.0-daymet-byHRU-onprem',
 'nhm-v1.0-daymet-byHW-musk-onprem',
 'nhm-v1.0-daymet-byHW-musk-obs-onprem',
 'nhm-v1.0-daymet-byHW-noroute-onprem',
 'nhm-v1.0-daymet-byHW-noroute_obs-onprem']

In [6]:
list(cat)

['conus404-hourly-onprem',
 'conus404-hourly-cloud',
 'conus404-hourly-osn',
 'conus404-daily-diagnostic-onprem',
 'conus404-daily-diagnostic-cloud',
 'conus404-daily-diagnostic-osn',
 'conus404-daily-onprem',
 'conus404-daily-cloud',
 'conus404-daily-osn',
 'conus404-monthly-onprem',
 'conus404-monthly-cloud',
 'conus404-monthly-osn',
 'conus404-hourly-ba-osn',
 'conus404-daily-ba-osn']

In [7]:
list(cat3)

['nhm-v1.1-gridmet-byHRU-onprem',
 'nhm-v1.1-gridmet-byHW-onprem',
 'nhm-v1.1-gridmet-byHWobs-onprem']

cat = hytest_cat['nhm-v1.1-gridmet-catalog']
list(cat)

In [8]:
## Select the dataset you want to read into your notebook and preview its metadata
dataset = 'conus404-daily-osn' 
dataset2 = 'nhm-v1.0-daymet-byHW-musk-onprem' 
dataset3 = 'nhm-v1.1-gridmet-byHRU-onprem'
list(dataset)
list(dataset2)
list(dataset3)
cat[dataset]
cat2[dataset2]
cat3[dataset3]

nhm-v1.1-gridmet-byHRU-onprem:
  args:
    consolidated: false
    storage_options:
      fo: /caldera/hovenweep/projects/usgs/water/impd/hytest/nhm/nhm_v1.1/gm_byHRU/nhm_v1.1_gm_byHRU_combined.json
    urlpath: reference://
  description: National Hydrologic Model version 1.1 model output variables using
    byHRU calibrated parameters with gridmet forcings
  driver: intake_xarray.xzarr.ZarrSource
  metadata:
    catalog_dir: https://raw.githubusercontent.com/hytest-org/hytest/main/dataset_catalog/subcatalogs


In [9]:
print(f"Reading {dataset} metadata...", end='')
ds = cat[dataset].to_dask().metpy.parse_cf()
print("done")


# print(f"Reading {dataset3} metadata...", end='')
# ds3 = cat3[dataset3].to_dask().metpy.parse_cf()
# print("done")


# ds2 = cat2[dataset2].to_dask().metpy.parse_cf()
# Examine the grid data structure for SNOW: 
# ds.ACECAN

Reading conus404-daily-osn metadata...done


In [10]:
crs = ds['ACRAINLSM'].metpy.cartopy_crs
crs

<Projected CRS: +proj=lcc +ellps=sphere +a=6370000.0 +b=6370000.0  ...>
Name: unknown
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- undefined
Coordinate Operation:
- name: unknown
- method: Lambert Conic Conformal (2SP)
Datum: unknown
- Ellipsoid: unknown
- Prime Meridian: Greenwich

In [78]:
%%time
da = ds.ACRAINLSM.sel(time='2016-09-22').load()
### NOTE: the `load()` is dask-aware, so will operate in parallel if
### a cluster has been started. 

CPU times: total: 969 ms
Wall time: 1.81 s


In [60]:
# !pip install geoviews

In [61]:
da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

:DynamicMap   []
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [lon,lat]   (ACRAINLSM)

In [83]:
import geoviews as gv 
import cartopy.crs as ccrs
lon_range = (-92, -94)
lat_range = (41.5, 42.35)
WATERSHED = "Ioway Creek"
shapefile_path = f'C:\\Users\\adi10136\\Desktop\\Runoff Analysis\\Shp\\{WATERSHED}\\layers\\globalwatershed.shp'
Ioway_Creekgdf = gpd.read_file(shapefile_path)
# Ioway_Creekgdf = Ioway_Creekgdf.to_crs(ccrs.LambertConformal())

# cartopy.crs.LambertConformal
Ioway_Creekgdf = Ioway_Creekgdf.to_crs(epsg=4326)

# Define the CRS for Lambert Conformal projection
# polygon_gdf.to_crs(ccrs.LambertConformal())


# Reproject the shapefile to Lambert Conformal projection

# Plot the shapefile using hvplot
Ioway_creek_plot = Ioway_Creekgdf.hvplot(geo=True, line_width=2, alpha=0.7)

# Plot the data
# plot = da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)
# plot = plot.opts(xlim=lon_range, ylim=lat_range)
# plot.opts(aspect='equal')
plot = da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis',
                          xlim=lon_range, ylim=lat_range).opts('Image', alpha=0.8)


# plot = da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis',
#                           project=True, crs=ccrs.LambertConformal(central_latitude=25, central_longitude=-95),
#                           xlim=lon_range, ylim=lat_range).opts('Image', alpha=0.6)

# # Add a USA basemap using Stamen Terrain
# basemap = gv.tile_sources.StamenTerrain

# # Overlay the basemap on the plot
# plot = plot * basemap.opts(alpha=0.5)
# Show the plot
combined_plot = Ioway_creek_plot * plot
combined_plot




:DynamicMap   []
   :Overlay
      .Polygons.I :Polygons   [Longitude,Latitude]
      .WMTS.I     :WMTS   [Longitude,Latitude]
      .Image.I    :Image   [lon,lat]   (ACRAINLSM)

## Time series with plots daily averages - Agregate years - Sum - Spatial averages (Daily)

### Plots multiple years /  Or / One year Spatial agreg

In [15]:
start_date = '2016-01-01 00:00'
end_date = '2016-06-30 23:59' 
print(coordinates)
Ioway_Creek = Polygon(coordinates)
x_list, y_list = [], []
for lon, lat in coordinates:
    x, y = crs.transform_point(lon, lat, src_crs=ccrs.PlateCarree()) 
    x_list.append(x)
    y_list.append(y)
# print(x_list, y_list)
polygon_gdf = gpd.GeoDataFrame(geometry=[Ioway_Creek], crs="EPSG:4326")
polygon_gdf = polygon_gdf.to_crs(ccrs.LambertConformal())
# Mask your data using the polygon
# %%time
# da = ds.ACRAINLSM.sel(x=x, y=y, method='nearest').sel(time=slice(start_date, end_date)).load()
da = ds.ACRAINLSM.sel(x=x, y=y, method='nearest').sel(time=slice('2016-01-01 00:00','2016-12-30 00:00')).load()
masked_data = da.where(da.lon, da.lat, lambda lon, lat: polygon_gdf.geometry.contains(Point(lon, lat)))
mean_values = masked_data.mean()

# mean_values.plot()
# da.hvplot(x='time', grid=True)



#  <===== Ames =====>
# lat,lon = 42.05,-93.53   
# x, y = crs.transform_point(lon, lat, src_crs=ccrs.PlateCarree()) 
#print(x,y) # these vals are in LCC

# %%time
da = ds.ACRAINLSM.sel(x=x, y=y, method='nearest').sel(time=slice('2016-01-01 00:00','2016-12-31 00:00')).load()
da.hvplot(x='time', grid=True)

((-93.79713650267362, 42.32456378704344), (-93.79713536578073, 42.324473734198016), (-93.79664994967764, 42.324477107767095), (-93.7966488134821, 42.32438705490967), (-93.79628475186925, 42.324389583730195), (-93.796283616198, 42.32429953086338), (-93.79604090877616, 42.32430121609639), (-93.79603977345619, 42.32421116322284), (-93.79579706635963, 42.32421284793691), (-93.79579593139088, 42.324122795056645), (-93.7955532246196, 42.32412447925178), (-93.79555209000213, 42.3240344263648), (-93.79543073678174, 42.32403526826709), (-93.79542960234248, 42.323945215376), (-93.79518689623214, 42.323946898790126), (-93.79518576214416, 42.32385684589233), (-93.79494305635909, 42.323858528787525), (-93.79494192262234, 42.323768475882964), (-93.7946992171626, 42.32377015825923), (-93.7946980837771, 42.32368010534799), (-93.79445537864264, 42.32368178720536), (-93.79445424560836, 42.32359173428736), (-93.79178449156804, 42.323610200760044), (-93.7917833623455, 42.32352014778269), (-93.791419305301

:Curve   [time]   (ACRAINLSM)

In [84]:
import geopandas as gpd
import hvplot.pandas  # Import hvplot extension for Pandas
import cartopy.crs as ccrs

# Load the shapefile
# shapefile_path = 'path_to_your_shapefile.shp' # needed if you want to specify before the path
Ioway_Creekgdf = gpd.read_file(f'C:\\Users\\adi10136\\Desktop\\Runoff Analysis\\Shp\\{WATERSHED}\\layers\\globalwatershed.shp')
#  polygon_gdf = gpd.GeoDataFrame(geometry=[Ioway_Creek], crs="EPSG:4326")

# Plot the shapefile using hvplot
Ioway_Creekgdf.hvplot(geo=True, line_width=2, alpha=0.7)

# Load the raster dataset using dask
ds = cat[dataset].to_dask().metpy.parse_cf()

# Select the desired time slice
da = ds.ACRAINLSM.sel(time='2017-08-29').load()

# Get the nodata value from the original raster dataset
nodata = da.attrs.get('_FillValue')  # Assuming the nodata value is the same for all bands

# Perform the clipping
clipped_data = mask(da.values, Ioway_Creekgdf.geometry, crop=True, nodata=nodata)

# Convert the clipped data to an xarray DataArray
clipped_data_array = xr.DataArray(clipped_data)

# Visualize the clipped raster using hvplot
clipped_data_array.hvplot(image='x', cmap='viridis', geo=True, crs=lambert_crs)


AttributeError: 'numpy.ndarray' object has no attribute 'nodata'

In [85]:

# Load the shapefile
WATERSHED = "Ioway Creek"
shapefile_path = f'C:\\Users\\adi10136\\Desktop\\Runoff Analysis\\Shp\\{WATERSHED}\\layers\\globalwatershed.shp'
Ioway_Creekgdf = gpd.read_file(shapefile_path)
# Ioway_Creekgdf = Ioway_Creekgdf.to_crs(ccrs.LambertConformal())

# cartopy.crs.LambertConformal
Ioway_Creekgdf = Ioway_Creekgdf.to_crs(epsg=4326)

# Define the CRS for Lambert Conformal projection
# polygon_gdf.to_crs(ccrs.LambertConformal())


# Reproject the shapefile to Lambert Conformal projection

# Plot the shapefile using hvplot
Ioway_Creekgdf.hvplot(geo=True, line_width=2, alpha=0.7)


:Polygons   [Longitude,Latitude]

In [16]:
import geoviews as gv 
import cartopy.crs as ccrs
from cartopy.feature import ShapelyFeature


on_range = (-95.67, -94)
lat_range = (28.92, 30)
# Plot the data
# plot = da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)
# plot = plot.opts(xlim=lon_range, ylim=lat_range)
# plot.opts(aspect='equal')
plot = da.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis',
                          xlim=lon_range, ylim=lat_range).opts('Image', alpha=0.8)


# Convert the polygon to a ShapelyFeature
polygon_feature = ShapelyFeature(polygon_gdf.geometry, ccrs.PlateCarree())

# Add the polygon to the plot
plot = plot * gv.feature.Feature(polygon_feature)

# Show the plot
plot.opts(aspect='equal')



DataError: The coordinates on the 'ACRAINLSM' DataArray do not match the provided key dimensions (kdims). The following coords were left unspecified: ['time']. If you are requesting a lower dimensional view such as a histogram cast the xarray to a columnar format using the .to_dataframe or .to_dask_dataframe methods before providing it to HoloViews.

In [ ]:
# Define the latitude and longitude coordinates
lat, lon = 42.05,-93.53 

# Transform the coordinates to Lambert Conformal Conic projection
x, y = crs.transform_point(lon, lat, src_crs=ccrs.PlateCarree())

# Select the dataset values nearest to the transformed coordinates and within the specified time range
da = ds.ACRAINLSM.sel(x=x, y=y, method='nearest').sel(time=slice('1993-01-01 00:00', '1993-12-31 00:00')).load()

# Accumulate the values along the time dimension
accumulated_values = np.cumsum(da, axis=0)

# Plot the accumulated values
accumulated_values.hvplot(x='time', grid=True)

# Print the accumulated values
print("Accumulated values along the time dimension:")
print(accumulated_values)


In [ ]:
%%time
ds_Dailysubset = ds[['T2', 'U10']].sel(time=slice('2016-01-02', '2016-01-03'))
# Daily = ds_Dailysubset(time="24H").mean

In [ ]:
ds.ACRAINLSM
sub_daily = ds_Dailysubset.resample(time="24H").mean()

In [ ]:
sub_daily

sub_daily.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', alpha=0.7, cmap='turbo')

In [86]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import geopandas as gpd
from pyproj import Geod
import matplotlib.pyplot as plt
import numpy as np
from scipy.stats import linregress
import ee
import json
import geemap
import folium
from PIL import Image
import io
import ipywidgets as widgets
from ipyleaflet import Map, GeoJSON, Marker
import base64
from io import BytesIO
import geemap.geemap as geemap

In [87]:
# Authenticate Earth Engine using your Google Account
ee.Authenticate()
ee.Initialize()

Enter verification code: 4/1AeaYSHA-yDcLFe8bdGv0jPUvfpNgEXsHl1WbY9b1azuE5tFUbfKV8dPDz28

Successfully saved authorization token.


In [90]:
startdate = '2017-08-27'
enddate = '2017-08-29'


# GRIDMET: University of Idaho Gridded Surface Meteorological Dataset (Database of precipitation)
dataset2 = ee.ImageCollection('IDAHO_EPSCOR/GRIDMET').filterDate(startdate, enddate)
pr = dataset2.select(['pr']).sum()

# PRISM: PRISM Daily Spatial Climate Dataset AN81d
dataset3 = ee.ImageCollection('OREGONSTATE/PRISM/AN81d').filterDate(startdate, enddate)
pr2 = dataset3.select(['ppt']).sum()

# Daymet V4: Daily Surface Weather and Climatological Summaries
dataset4 = ee.ImageCollection('NASA/ORNL/DAYMET_V4').filterDate(startdate, enddate)
pr3 = dataset4.select(['prcp']).sum()

In [93]:
import geemap
import numpy as np
import xarray as xr

ds = cat[dataset].to_dask().metpy.parse_cf()
# %%time
# da = ds.ACRAINLSM.sel(time='2017-08-29').load()
# acrainlsm = da['ACRAINLSM']
### NOTE: the `load()` is dask-aware, so will operate in parallel if
### a cluster has been started. 
array = acrainlsm.values
ee_image = geemap.ee.Image(array.tolist())
ee_image = ee_image.reproject(crs='EPSG:4326', scale=1000)

NameError: name 'acrainlsm' is not defined

In [ ]:
Map = geemap.Map()
viridisPalette = ['440154', '482878', '3e4a89', '31688e', '26838f', '1f9e89', '35b779', '6ece58', 'b5de2b', 'fde725'];

P_vis = {
'min': 0,
'max': 1000,
'palette': viridisPalette   
# 'palette': ['2d4c6e', '80c256', '61b95c', '42b062', '45b677', '55cece', '4db4ba', '459aa7', '3d8094', '356681', 'FFFF01'
#             , '49bc8d', '4dc2a2', '51c8b8',
#     '55cece', '4db4ba', '459aa7', '3d8094', '356681', '2d4c6e'
           ,
'opacity':0.7}

# 'bed44b', '9fcb51', '80c256', '61b95c', '42b062', '45b677'

legend_dict = {
    '0 - 100': '#2d4c6e',
    '100 - 200': '#80c256',
    '200 - 300': '#61b95c',
    '300 - 400': '#42b062',
    '400 - 500': '#45b677',
    '500 - 600': '#55cece',
    '600 - 700': '4db4ba',
    '700 - 800': '#459aa7',
    '800 - 900': '#3d8094',
    '900 - 1000': '#356681',
    '1000 - 1100': '#FFFF01',
#     '1100 - 1200': '#49bc8d',
#     '1200 - 1300': '#4dc2a2',
#     '1300 - 1400': '#51c8b8',
#     '1400 - 1500': '#55cece',
#     '1500 - 1600': '#4db4ba',
#     '1600 - 1700': '#459aa7',
#     '1700 - 1800': '#3d8094',
#     '1800 - 1900': '#356681',
#     '1900 - 2000': '#2d4c6e',
}
Map.add_legend(legend_title='Precipitation (mm)', legend_dict=legend_dict)
Map.addLayer(pr, P_vis, 'GRIDMET Precipitation (mm)')
Map.addLayer(pr2, P_vis, 'PRISM Precipitation (mm)')
Map.addLayer(pr3, P_vis, 'DAYMET Precipitation (mm)')

grid = geemap.latlon_grid(lat_step=10, lon_step=10, west=-180, east=180, south=-85, north=85)
Map.addLayer(grid, {}, "Coordinate Grid")
# Map.add_labels(
#     grid,
#     "latitude",
#     font_size="8pt",
#     font_color="blue",
#     font_family="arial",
#     font_weight="bold",
#     x='longitude',
#     y='latitude',
#     draggable=True,
#     layer_name='Labels'
# )
# Map.add_labels(
#     grid,
#     "longitude",
#     font_size="8pt",
#     font_color="blue",
#     font_family="arial",
#     font_weight="bold",
#     x='longitude',
#     y='latitude',
#     draggable=True,
#     layer_name='Labels'
# )
states = ee.FeatureCollection("TIGER/2018/States")

filterstate1 = ee.Filter.eq('NAME', 'Texas');


# #===============================================#

# url = "https://app.globus.org/file-manager?origin_id=39161d64-419d-4cc4-853f-f6e737644eb4&origin_path=%2Fwrfconus404%2FWY2017%2Fwrfxtrm%2F"
# filename = "wrfxtrm_conusii_201708.tar"

# m = geemap.Map(layer_ctrl=True)
# m.add_netcdf(
#     filename,
#     variables=["v_wind"],
#     palette="coolwarm",
#     shift_lon=True,
#     layer_name="v_wind",
# )
# m.add_geojson(geojson, layer_name="Countries")
# m
# #===============================================#

# Map = geemap.Map(center=(40, -100), zoom=4)
# Map.addLayer(ee_image, {'min': 0, 'max': 100}, 'Raster Layer') 
# Map.addLayerControl()

state1 = states.filter(filterstate1);
Map.centerObject(state1)
Map
